# Compute medians in SQL

In [ ]:
from data201 import db_connection, df_query

In [ ]:
conn = db_connection(config_file = 'Median.ini')
cursor = conn.cursor()

## SQL: Odd count of values

In [ ]:
cursor.execute('DROP TABLE IF EXISTS test_values')

sql = """
    CREATE TABLE test_values
    (
        id INT NOT NULL AUTO_INCREMENT,
        value INT NOT NULL,
        PRIMARY KEY(id)
    )
    """

cursor.execute(sql)

In [ ]:
sql = ( """
        INSERT INTO test_values(value)
        VALUES (%s)
        """
      )

original_list_odd = [ 15, 6, 20, 13, 8, 2, 6 ]
values = list(zip(original_list_odd))

cursor.executemany(sql, values)
conn.commit()

df_query(conn, 'SELECT * FROM test_values')

#### Use window functions to count the number of values and to assign an index to each row after sorting.

In [ ]:
df_query(conn,
    """
    SELECT COUNT(*) OVER () AS row_count,
           id,
           ROW_NUMBER() OVER (ORDER BY value) AS row_index,
           value
    FROM test_values
    """
)

#### Make the above a CTE. Then the median is the value with the middle row index.

In [ ]:
df_query(conn,
    """
    WITH indexed_rows AS
    (
    SELECT COUNT(*) OVER () AS row_count,
           id,
           ROW_NUMBER() OVER (ORDER BY value) AS row_index,
           value
    FROM test_values
    )
    SELECT value AS median_value
    FROM indexed_rows
    WHERE row_index = FLOOR((row_count + 1)/2)
    """
)

## SQL: Even count of values

In [ ]:
cursor.execute(
    """
    INSERT INTO test_values(value)
    VALUE (25)
    """
)

conn.commit()
df_query(conn, 'SELECT * FROM test_values')

#### Use window functions to count the number of values and to assign an index to each row after sorting.

In [ ]:
df_query(conn,
    """
    SELECT COUNT(*) OVER () AS row_count,
           id,
           ROW_NUMBER() OVER (ORDER BY value) AS row_index,
           value
    FROM test_values
    """
)

#### Make the above a CTE. Then the median is the average of the two value with the two middle row indexes.

In [ ]:
df_query(conn,
    """
    WITH indexed_rows AS
    (
        SELECT COUNT(*) OVER () AS row_count,
               id,
               ROW_NUMBER() OVER (ORDER BY value) AS row_index,
               value
        FROM test_values
    )
    SELECT AVG(value) AS median_value
    FROM indexed_rows
    WHERE row_index IN (FLOOR((row_count + 1)/2), CEIL((row_count + 1)/2))
    """
)

## View to calculate the median

In [ ]:
cursor.execute('DROP VIEW IF EXISTS median_view')

cursor.execute(
    """
    CREATE VIEW median_view AS
    WITH indexed_rows AS
    (
        SELECT COUNT(*) OVER () AS row_count,
               id,
               ROW_NUMBER() OVER (ORDER BY value) AS row_index,
               value
        FROM test_values
    )
    SELECT AVG(value) AS median_value
    FROM indexed_rows
    WHERE row_index IN (FLOOR((row_count + 1)/2), CEIL((row_count + 1)/2))
    """
)

In [ ]:
df_query(conn, 'SELECT * FROM median_view')

## Any number of values
#### Will the view also work for an odd number of values?

In [ ]:
cursor.execute(
    """
    DELETE FROM test_values
    WHERE value = 25
    """
)

conn.commit()
df_query(conn, 'SELECT * FROM test_values')

#### Yes, if the number of values is odd, row indexes `FLOOR((row_count + 1)/2)` and `CEIL((row_count + 1)/2)` are equal, and so we'll end up taking the average of two copies of the same median value.

In [ ]:
df_query(conn, 'SELECT * FROM median_view')

In [ ]:
cursor.close()
conn.close()